## Imports & Defining Path to The Delta Table

In [ ]:
# import pyspark functions
from pyspark.sql.functions import *
from pyspark.sql.types import StructType, StructField, IntegerType, StringType, TimestampType, FloatType
# import URL processing
import urllib
     
# Define the path to the Delta table
delta_table_path = "dbfs:/user/hive/warehouse/authentication_credentials"

# Read the Delta table to a Spark DataFrame
aws_keys_df = spark.read.format("delta").load(delta_table_path)

##Read Credentials from Data Table

In [ ]:

# list tables in filestore to get name of credentials file
dbutils.fs.ls("/FileStore/tables")

Out[26]: [FileInfo(path='dbfs:/FileStore/tables/0ed442ca38ad_user_table/', name='0ed442ca38ad_user_table/', size=0, modificationTime=1709595856369),
 FileInfo(path='dbfs:/FileStore/tables/authentication_credentials.csv/', name='authentication_credentials.csv/', size=0, modificationTime=1709595856369),
 FileInfo(path='dbfs:/FileStore/tables/csv_files/', name='csv_files/', size=0, modificationTime=1709595856369),
 FileInfo(path='dbfs:/FileStore/tables/date_details.json', name='date_details.json', size=284166, modificationTime=1703945051000),
 FileInfo(path='dbfs:/FileStore/tables/downloaded_file.json', name='downloaded_file.json', size=48, modificationTime=1703945574000),
 FileInfo(path='dbfs:/FileStore/tables/downloaded_file2.json', name='downloaded_file2.json', size=60, modificationTime=1703954387000),
 FileInfo(path='dbfs:/FileStore/tables/geo_dirty.csv/', name='geo_dirty.csv/', size=0, modificationTime=1709595856369),
 FileInfo(path='dbfs:/FileStore/tables/json_files/', name='json_files/', size=0, modificationTime=1709595856369),
 FileInfo(path='dbfs:/FileStore/tables/maya/', name='maya/', size=0, modificationTime=1709595856369),
 FileInfo(path='dbfs:/FileStore/tables/pin_dirty.csv/', name='pin_dirty.csv/', size=0, modificationTime=1709595856369),
 FileInfo(path='dbfs:/FileStore/tables/single_json_file.json', name='single_json_file.json', size=293, modificationTime=1701857903000),
 FileInfo(path='dbfs:/FileStore/tables/test_credentials.csv', name='test_credentials.csv', size=99, modificationTime=1704283321000),
 FileInfo(path='dbfs:/FileStore/tables/user_dirty.csv/', name='user_dirty.csv/', size=0, modificationTime=1709595856369)]

In [ ]:
# Get the AWS access key and secret key from the spark dataframe
ACCESS_KEY = aws_keys_df.select('Access key ID').collect()[0]['Access key ID']
SECRET_KEY = aws_keys_df.select('Secret access key').collect()[0]['Secret access key']
# Encode the secrete key
ENCODED_SECRET_KEY = urllib.parse.quote(string=SECRET_KEY, safe="")

## Get & Deserialise Streams & Structure Table  

In [ ]:
#Pin Streaming Data

from pyspark.sql.functions import from_json, col, base64
from pyspark.sql.types import StructType, StructField, IntegerType, TimestampType, FloatType, StringType
from pyspark.streaming.kinesis import KinesisUtils, InitialPositionInStream

kinesisStreamName = "streaming-0a07b87658a3-pin"
regionName = "us-east-1"

# Read data from Kinesis stream using structured streaming
streaming_df_pin_kinesis = spark.readStream \
    .format("kinesis") \
    .option("streamName", kinesisStreamName) \
    .option("regionName", regionName) \
    .option("initialPosition", "TRIM_HORIZON") \
    .option("format", "json") \
    .option("awsAccessKey", ACCESS_KEY) \
    .option("awsSecretKey", SECRET_KEY) \
    .option("inferSchema", "true") \
    .load()

# define the schema for the table (must use the correct column names)
schema = StructType([
    StructField("index", IntegerType()),
    StructField("unique_id", StringType()),
    StructField("title", StringType()),
    StructField("description", StringType()),
    StructField("poster_name", StringType()),
    StructField("follower_count", StringType()),
    StructField("tag_list", StringType()),
    StructField("is_image_or_video", StringType()),
    StructField("image_src", StringType()),
    StructField("downloaded", IntegerType()),
    StructField("save_location", StringType()),
    StructField("category", StringType())
])

# Define a UDF to deserialize the data column
deserialise_udf_pin = from_json(col("data").cast("string"), schema)

# Apply the UDF and select the desired columns
streaming_df_pin = streaming_df_pin_kinesis.withColumn("cast_data_pin", deserialise_udf_pin) \
    .select("cast_data_pin.index", "cast_data_pin.unique_id", "cast_data_pin.title", "cast_data_pin.description", "cast_data_pin.poster_name", "cast_data_pin.follower_count", "cast_data_pin.tag_list", "cast_data_pin.is_image_or_video", "cast_data_pin.image_src", "cast_data_pin.downloaded", "cast_data_pin.save_location", "cast_data_pin.category")

display(streaming_df_pin)

index unique_id title description poster_name follower_count tag_list is_image_or_video image_src downloaded save_location category 7528 fbe53c66-3442-4773-b19e-d3ec6f54dddf No Title Data Available No description available Story format User Info Error User Info Error N,o, ,T,a,g,s, ,A,v,a,i,l,a,b,l,e multi-video(story page format) Image src error. 0 Local save in /data/mens-fashion mens-fashion 2863 9bf39437-42a6-4f02-99a0-9a0383d8cd70 25 Super Fun Summer Crafts for Kids - Of Life and Lisa Keep the kids busy this summer with these easy diy crafts and projects. Creative and… Of Life & Lisa | Lifestyle Blog 124k Summer Crafts For Kids,Fun Crafts For Kids,Summer Kids,Toddler Crafts,Crafts To Do,Diy For Kids,Summer Snow,Diys For Summer,Craft Ideas For Girls image https://i.pinimg.com/originals/b3/bc/e2/b3bce2964e8c8975387b39660eed5f16.jpg 1 Local save in /data/diy-and-crafts diy-and-crafts 5730 1e1f0c8b-9fcf-460b-9154-c775827206eb Island Oasis Coupon Organizer Description Coupon Organizer in a fun colorful fabric -island oasis, Great Size for the "basic" couponer - holds up to 500 coupons with ease, and is made long enough so that you…  Consuelo Aguirre 0 Grocery Items,Grocery Coupons,Care Organization,Coupon Organization,Extreme Couponing,Couponing 101,Life Binder,Save My Money,Love Coupons image https://i.pinimg.com/originals/65/bb/ea/65bbeaf458907bb079317d8303c4fa0e.jpg 1 Local save in /data/finance finance 8304 5b6d0913-25e4-43ab-839d-85d5516f78a4 The #1 Reason You’re Not His Priority Anymore - Matthew Coast #lovequotes #matchmaker #matchmadeinheaven #loveyourself #respectyourself Commitment Connection 51k Wise Quotes,Quotable Quotes,Words Quotes,Wise Words,Quotes To Live By,Great Quotes,Motivational Quotes,Inspirational Quotes,Funny Quotes image https://i.pinimg.com/originals/c6/64/ee/c664ee71524fb5a6e7b7b49233f93b43.png 1 Local save in /data/quotes quotes 8731 ea760f71-febf-4023-b592-d17396659039 20 Koi Fish Tattoos For Lucky Men Koi fish tattoos are a popular choice for men who want to make a statement, thanks to their rich symbolism and bold design. TheTrendSpotter 211k Dr Tattoo,Wörter Tattoos,Pisces Tattoos,Tatoo Art,Dream Tattoos,Dope Tattoos,Mini Tattoos,Finger Tattoos,Body Art Tattoos image https://i.pinimg.com/originals/8a/0c/0a/8a0c0a7b6236565c519acd41ad1a52c0.jpg 1 Local save in /data/tattoos tattoos 1313 44662045-e891-4821-8a19-ebe7eedd371a Liquid Lash Extensions Mascara Instantly create the look of lash extensions with this award-winning, best-selling mascara that won't clump, flake or smudge. Available in 3 shades! Thrive Causemetics 43k N,o, ,T,a,g,s, ,A,v,a,i,l,a,b,l,e video https://i.pinimg.com/videos/thumbnails/originals/69/84/e2/6984e20f3e262098fa9c0614c3453254.0000001.jpg 1 Local save in /data/beauty beauty 4315 21b59ba9-829d-4c33-8c27-4cd4c56d26b8 Podcasts for Teachers or Parents of Teenagers Podcasts for Teachers or Parents of Teenagers: Teaching teens middle school and high school can feel joyful and rewarding most days, but can also frustrate you with one challeng…  Math Giraffe 25k Middle School Classroom,High School Students,High School Teachers,Middle School Tips,High School Counseling,Ela Classroom,High School Science,Future Classroom,Google Classroom image https://i.pinimg.com/originals/50/19/31/501931a27ee4d076658980851b995b2c.jpg 1 Local save in /data/education education 10794 c4bd2577-a7bb-4409-bb7a-17d5ed7e1cf1 TireBuyer Nissan GT-R. Sick. Ray Uyemura 437 Lowrider,Old Vintage Cars,Antique Cars,Austin Martin,Nissan Gtr Black,Jaguar,1959 Cadillac,Cadillac Ct6,Old School Cars image https://i.pinimg.com/originals/0d/29/9f/0d299f3df020395aa7ce8387f40fbeed.jpg 1 Local save in /data/vehicles vehicles 5494 8fb2af68-543b-4639-8119-de33d28706ed Dave Ramsey's 7 Baby Steps: What Are They And Will They Work For You If you love budgeting, make sure to give Dave Ramsey's 7 Baby Steps a try. Follow these steps to begin your debt snowball, build an emergency fund, invest and reach riches. I ca…  Living Low Key

In [ ]:
#Geo Streaming Data

from pyspark.sql.functions import from_json, col, base64
from pyspark.sql.types import StructType, StructField, IntegerType, TimestampType, FloatType, StringType
from pyspark.streaming.kinesis import KinesisUtils, InitialPositionInStream

kinesisStreamName = "streaming-0a07b87658a3-geo"
regionName = "us-east-1"

# Read data from Kinesis stream using structured streaming
streaming_df_geo_kinesis = spark.readStream \
    .format("kinesis") \
    .option("streamName", kinesisStreamName) \
    .option("regionName", regionName) \
    .option("initialPosition", "TRIM_HORIZON") \
    .option("format", "json") \
    .option("awsAccessKey", ACCESS_KEY) \
    .option("awsSecretKey", SECRET_KEY) \
    .option("inferSchema", "true") \
    .load()


# Define the schema for the table
schema = StructType([
    StructField("ind", IntegerType()),
    StructField("timestamp", TimestampType()),
    StructField("latitude", FloatType()),
    StructField("longitude", FloatType()),
    StructField("country", StringType())
])

# Define a UDF to deserialize the data column
deserialise_udf_geo = from_json(col("data").cast("string"), schema)

# Apply the UDF and select the desired columns
streaming_df_geo = streaming_df_geo_kinesis.withColumn("cast_data_geo", deserialise_udf_geo) \
    .select("cast_data_geo.ind", "cast_data_geo.timestamp", "cast_data_geo.latitude", "cast_data_geo.longitude", "cast_data_geo.country")

display(streaming_df_geo)

ind timestamp latitude longitude country 7528 2020-08-28T03:52:47.000+0000 -89.9787 -173.293 Albania 2863 2020-04-27T13:34:16.000+0000 -5.34445 -177.924 Armenia 5730 2021-04-19T17:37:03.000+0000 -77.015 -101.437 Colombia 8304 2019-09-13T04:50:29.000+0000 -28.8852 -164.87 French Guiana 8731 2020-07-17T04:39:09.000+0000 -83.104 -171.302 Aruba 1313 2018-06-26T02:39:25.000+0000 77.0447 61.9119 Maldives 4315 2019-12-15T03:51:28.000+0000 -45.8508 66.1003 Cote d'Ivoire 10794 2022-01-01T02:26:50.000+0000 -89.5236 -154.567 Cocos (Keeling) Islands 5494 2021-07-21T02:02:35.000+0000 -82.6768 -129.202 Bulgaria 5069 2021-03-20T09:32:44.000+0000 -63.0063 -157.474 Azerbaijan 2923 2019-09-08T22:53:09.000+0000 -84.6302 -164.507 Cote d'Ivoire 3089 2018-02-28T05:31:29.000+0000 -89.9787 -173.293 Albania 6063 2021-07-20T09:02:47.000+0000 -89.1797 -174.015 Anguilla 3454 2021-07-25T02:20:29.000+0000 -0.375174 49.8106 Cambodia 7554 2019-03-20T03:15:07.000+0000 -51.2172 -77.9768 Sudan 6145 2019-12-05T02:09:44.000+0000 -65.9079 -143.845 Mozambique 10625 2018-07-13T11:51:15.000+0000 -84.4944 -81.0613 Jamaica 2959 2019-08-19T08:22:02.000+0000 -68.0095 -157.227 Angola 9875 2020-03-20T13:03:18.000+0000 -74.3382 -110.484 Barbados 2418 2022-05-27T11:30:59.000+0000 -88.4642 -171.061 Antarctica (the territory South of 60 deg S) 3156 2018-01-13T19:33:49.000+0000 -84.738 -160.795 Armenia 428 2020-09-27T18:46:41.000+0000 -83.4105 -150.788 Bangladesh 7343 2018-08-06T12:17:07.000+0000 -65.4428 -161.684 Australia 2074 2019-11-03T05:41:59.000+0000 -52.3213 -50.11 Central African Republic 9979 2018-07-18T19:01:46.000+0000 14.9967 -120.682 Dominican Republic 10138 2019-08-03T00:59:29.000+0000 -72.142 -74.3545 Austria 9672 2019-11-03T13:15:52.000+0000 79.4658 -69.4133 India 8653 2022-04-11T18:30:19.000+0000 48.4569 -139.658 Seychelles 8887 2021-09-19T05:27:43.000+0000 -28.0137 -160.708 Botswana 7922 2021-01-27T09:14:19.000+0000 -88.0974 -172.052 Antigua and Barbuda 1014 2022-02-03T22:05:34.000+0000 81.1477 69.3538 Tonga 4913 2019-03-08T06:45:39.000+0000 -84.3768 -157.544 Aruba 4137 2019-06-23T22:16:34.000+0000 -55.3079 108.918 Australia 7166 2022-07-25T03:07:37.000+0000 -86.4063 -136.657 Aruba 9546 2018-02-10T06:16:40.000+0000 -70.0295 -155.428 Austria 2411 2020-11-15T17:10:07.000+0000 -71.6856 -179.126 Albania 9590 2019-05-20T19:48:48.000+0000 -64.3876 -174.281 Algeria 2698 2021-11-24T08:33:51.000+0000 -72.7174 24.169 Egypt 4508 2019-01-04T11:15:27.000+0000 69.1858 -76.0761 Philippines 831 2021-06-23T23:16:10.000+0000 -43.7816 -66.1592 Congo 5076 2019-05-05T16:22:23.000+0000 -70.7195 -91.1935 Germany 10663 2019-07-25T18:53:51.000+0000 -27.3474 -162.83 Saint Kitts and Nevis 5468 2020-05-16T23:17:50.000+0000 -83.544 33.9473 Isle of Man 205 2020-07-08T14:10:38.000+0000 -75.8378 -163.945 Barbados 7790 2018-07-31T08:19:15.000+0000 -43.692 64.9839 Papua New Guinea 8606 2021-03-28T14:54:07.000+0000 -88.0974 -172.052 Antigua and Barbuda 9759 2017-12-30T13:05:49.000+0000 -77.9744 -106.258 American Samoa 719 2018-10-29T04:05:12.000+0000 -38.4062 -154.323 Armenia 1704 2018-11-29T04:46:39.000+0000 -56.8702 -93.6232 Christmas Island 2482 2019-09-13T08:20:13.000+0000 63.4563 -164.709 Bermuda 8930 2021-09-29T13:25:49.000+0000 -89.4739 -176.154 Argentina 7294 2018-02-12T08:06:28.000+0000 -76.2967 -136.501 Australia 808 2019-01-03T15:43:12.000+0000 -71.6856 -179.126 Albania 771 2018-06-21T08:42:57.000+0000 -29.1712 -107.111 Montserrat 4076 2019-06-07T20:13:50.000+0000 -67.2157 27.8139 Mauritania 1545 2022-06-17T05:47:12.000+0000 -30.18 -72.3784 Anguilla 2293 2022-03-21T10:46:53.000+0000 -87.7946 -159.647 British Virgin Islands 10509 2019-03-06T12:21:56.000+0000 -67.187 -24.2977 Gibraltar 2015 2018-09-22T13:52:19.000+0000 -17.629 -177.685 Armenia 1094 2018-08-19T00:34:20.000+0000 -46.7328 -124.445 Armenia 603 2019-06-25T05:13:01.000+0000 14.0083 -141.603 Netherlands Antilles 7768 2018-05-25T21:34:19.000+0000 -88.355 -96.0131 Algeria 5630 2019-05-12T14:43:19.000+0000 -19.1403 -164.987 Bah

In [ ]:
#User Streaming Data

from pyspark.sql.functions import from_json, col, base64
from pyspark.sql.types import StructType, StructField, IntegerType, TimestampType, FloatType, StringType
from pyspark.streaming.kinesis import KinesisUtils, InitialPositionInStream

kinesisStreamName = "streaming-0a07b87658a3-user"
regionName = "us-east-1"

# Read data from Kinesis stream using structured streaming
streaming_df_user_kinesis = spark.readStream \
    .format("kinesis") \
    .option("streamName", kinesisStreamName) \
    .option("regionName", regionName) \
    .option("initialPosition", "TRIM_HORIZON") \
    .option("format", "json") \
    .option("awsAccessKey", ACCESS_KEY) \
    .option("awsSecretKey", SECRET_KEY) \
    .option("inferSchema", "true") \
    .load()


# Define the schema for the table
schema = StructType([
    StructField("ind", IntegerType()),
    StructField("first_name", StringType()),
    StructField("last_name", StringType()),
    StructField("age", StringType()),
    StructField("date_joined", TimestampType())
])

# Define a UDF to deserialize the data column
deserialise_udf_user = from_json(col("data").cast("string"), schema)

# Apply the UDF and select the desired columns
streaming_df_user = streaming_df_user_kinesis.withColumn("cast_data_user", deserialise_udf_user) \
    .select("cast_data_user.ind", "cast_data_user.first_name", "cast_data_user.last_name", "cast_data_user.age", "cast_data_user.date_joined")

display(streaming_df_user)


ind first_name last_name age date_joined 7528 Abigail Ali 20 2015-10-24T11:23:51.000+0000 2863 Dylan Holmes 32 2016-10-23T14:06:51.000+0000 5730 Rachel Davis 36 2015-12-08T20:02:43.000+0000 8304 Charles Berry 25 2015-12-28T04:21:39.000+0000 8731 Andrea Alexander 21 2015-11-10T09:27:42.000+0000 1313 Brittany Jones 32 2016-04-02T03:51:23.000+0000 4315 Michelle Prince 36 2015-12-20T16:38:13.000+0000 10794 Thomas Turner 34 2016-12-22T00:02:02.000+0000 5494 Anne Allen 27 2015-12-16T15:20:05.000+0000 5069 Amanda Ball 25 2016-01-13T17:36:30.000+0000 2923 Brian Nelson 26 2015-11-11T03:20:57.000+0000 3089 Abigail Ali 20 2015-10-24T11:23:51.000+0000 6063 Corey Andrews 23 2015-11-25T13:36:22.000+0000 3454 Robert Murphy 48 2017-09-26T16:31:56.000+0000 7554 Cheryl Huerta 20 2017-04-11T16:35:33.000+0000 6145 Emily Hawkins 30 2015-12-25T20:24:37.000+0000 10625 Christian Lang 32 2017-10-10T20:09:33.000+0000 2959 David Griffith 20 2016-01-07T19:49:22.000+0000 9875 Brendan Joseph 26 2015-12-20T10:28:00.000+0000 2418 Amanda Adams 20 2015-10-21T08:27:36.000+0000 3156 Andrew Baker 22 2015-12-21T08:06:54.000+0000 428 Claudia Adams 20 2015-11-28T02:20:29.000+0000 7343 Anne Clayton 24 2016-01-11T12:03:48.000+0000 2074 Annette Forbes 21 2016-01-03T15:42:12.000+0000 9979 Kaylee Miller 31 2016-11-09T19:50:51.000+0000 10138 Carol Silva 22 2015-12-31T14:57:02.000+0000 9672 Jennifer Hudson 22 2016-02-11T20:46:04.000+0000 8653 Tammy Davis 24 2016-03-09T10:48:14.000+0000 8887 Austin Rodriguez 24 2016-03-31T20:56:39.000+0000 7922 Denise Adams 21 2015-11-12T06:21:36.000+0000 1014 Gregory Ramsey 56 2016-10-15T17:21:39.000+0000 4913 Angela Brooks 24 2015-11-20T05:37:11.000+0000 4137 Michael Decker 59 2017-06-29T22:35:17.000+0000 7166 Alvin Adams 20 2016-01-01T13:50:40.000+0000 9546 Alex Barnes 20 2016-02-27T21:13:44.000+0000 2411 Aaron Bartlett 21 2015-11-24T02:15:36.000+0000 9590 Amanda Allen 22 2015-10-24T18:56:30.000+0000 2698 Kayla Burton 44 2017-06-21T19:53:27.000+0000 4508 Michael Carter 58 2016-06-03T23:35:30.000+0000 831 Aimee Collins 28 2016-06-16T02:06:38.000+0000 5076 Christopher Butler 20 2015-12-01T15:08:31.000+0000 10663 Julie Cox 23 2016-06-23T14:38:00.000+0000 5468 Lisa Gamble 20 2016-07-23T20:51:06.000+0000 205 Brett Bryant 20 2015-10-23T12:40:19.000+0000 7790 Michelle Gutierrez 39 2017-07-19T07:12:04.000+0000 8606 Denise Adams 21 2015-11-12T06:21:36.000+0000 9759 Daniel Brooks 25 2015-11-19T21:24:33.000+0000 719 Alicia Avila 20 2016-01-26T01:49:23.000+0000 1704 Barry Lynn 20 2015-10-28T05:00:33.000+0000 2482 David Moss 22 2016-03-01T07:11:48.000+0000 8930 Andrew Anderson 23 2015-11-28T11:52:37.000+0000 7294 Dawn Anderson 20 2016-12-31T00:06:36.000+0000 808 Aaron Bartlett 21 2015-11-24T02:15:36.000+0000 771 Brittany Butler 32 2016-03-10T04:11:31.000+0000 4076 Larry Pineda 20 2015-10-23T22:47:39.000+0000 1545 Jonathan Avila 46 2015-11-27T23:11:21.000+0000 2293 Alex Bean 24 2016-01-11T23:08:27.000+0000 10509 Brittany Thompson 49 2016-04-22T20:36:02.000+0000 2015 Christopher Bradshaw 27 2016-03-08T13:38:37.000+0000 1094 Ann Elliott 20 2016-07-02T02:32:30.000+0000 603 Brandon Jackson 44 2016-10-29T02:07:21.000+0000 7768 Christine Cortez 23 2015-12-01T18:15:02.000+0000 5630 Carlos Estrada 22 2016-02-09T17:01:38.000+0000 8578 Joe Pham 48 2017-06-01T23:13:27.000+0000 9936 Anthony Cantu 28 2016-11-15T10:40:03.000+0000 6844 Peter Roberts 30 2016-07-03T10:59:40.000+0000 3419 Aaron Jenkins 47 2017-04-26T03:26:23.000+0000 1268 Donna Campbell 32 2016-06-08T22:10:13.000+0000 6566 Alexander Perez 31 2017-08-04T14:30:22.000+0000 1555 Alexis Bennett 54 2016-05-15T04:22:01.000+0000 3729 Richard Edwards 52 2016-02-07T20:00:25.000+0000 6398 Christina Davenport 39 2016-06-29T20:43:59.000+0000 46 Erik Kelley 30 2016-01-06T09:58:56.000+0000 4988 Rhonda Durham 25 2017-07-20T05:51:23.000+0000 427 Jon Burke 25 2015-11-26T17:42:37.000+0000 3800 Adam Armstrong 20 2015-12-17T08:43:40.000+0000 159 Alison Bell 21 2016-01-07T08:11:35.000+0000 3599 Alexandria Alvarado 20 2015-1

## Displaying the Data Frames

In [ ]:
display(streaming_df_pin)


index unique_id title description poster_name follower_count tag_list is_image_or_video image_src downloaded save_location category 7528 fbe53c66-3442-4773-b19e-d3ec6f54dddf No Title Data Available No description available Story format User Info Error User Info Error N,o, ,T,a,g,s, ,A,v,a,i,l,a,b,l,e multi-video(story page format) Image src error. 0 Local save in /data/mens-fashion mens-fashion 2863 9bf39437-42a6-4f02-99a0-9a0383d8cd70 25 Super Fun Summer Crafts for Kids - Of Life and Lisa Keep the kids busy this summer with these easy diy crafts and projects. Creative and… Of Life & Lisa | Lifestyle Blog 124k Summer Crafts For Kids,Fun Crafts For Kids,Summer Kids,Toddler Crafts,Crafts To Do,Diy For Kids,Summer Snow,Diys For Summer,Craft Ideas For Girls image https://i.pinimg.com/originals/b3/bc/e2/b3bce2964e8c8975387b39660eed5f16.jpg 1 Local save in /data/diy-and-crafts diy-and-crafts 5730 1e1f0c8b-9fcf-460b-9154-c775827206eb Island Oasis Coupon Organizer Description Coupon Organizer in a fun colorful fabric -island oasis, Great Size for the "basic" couponer - holds up to 500 coupons with ease, and is made long enough so that you…  Consuelo Aguirre 0 Grocery Items,Grocery Coupons,Care Organization,Coupon Organization,Extreme Couponing,Couponing 101,Life Binder,Save My Money,Love Coupons image https://i.pinimg.com/originals/65/bb/ea/65bbeaf458907bb079317d8303c4fa0e.jpg 1 Local save in /data/finance finance 8304 5b6d0913-25e4-43ab-839d-85d5516f78a4 The #1 Reason You’re Not His Priority Anymore - Matthew Coast #lovequotes #matchmaker #matchmadeinheaven #loveyourself #respectyourself Commitment Connection 51k Wise Quotes,Quotable Quotes,Words Quotes,Wise Words,Quotes To Live By,Great Quotes,Motivational Quotes,Inspirational Quotes,Funny Quotes image https://i.pinimg.com/originals/c6/64/ee/c664ee71524fb5a6e7b7b49233f93b43.png 1 Local save in /data/quotes quotes 8731 ea760f71-febf-4023-b592-d17396659039 20 Koi Fish Tattoos For Lucky Men Koi fish tattoos are a popular choice for men who want to make a statement, thanks to their rich symbolism and bold design. TheTrendSpotter 211k Dr Tattoo,Wörter Tattoos,Pisces Tattoos,Tatoo Art,Dream Tattoos,Dope Tattoos,Mini Tattoos,Finger Tattoos,Body Art Tattoos image https://i.pinimg.com/originals/8a/0c/0a/8a0c0a7b6236565c519acd41ad1a52c0.jpg 1 Local save in /data/tattoos tattoos 1313 44662045-e891-4821-8a19-ebe7eedd371a Liquid Lash Extensions Mascara Instantly create the look of lash extensions with this award-winning, best-selling mascara that won't clump, flake or smudge. Available in 3 shades! Thrive Causemetics 43k N,o, ,T,a,g,s, ,A,v,a,i,l,a,b,l,e video https://i.pinimg.com/videos/thumbnails/originals/69/84/e2/6984e20f3e262098fa9c0614c3453254.0000001.jpg 1 Local save in /data/beauty beauty 4315 21b59ba9-829d-4c33-8c27-4cd4c56d26b8 Podcasts for Teachers or Parents of Teenagers Podcasts for Teachers or Parents of Teenagers: Teaching teens middle school and high school can feel joyful and rewarding most days, but can also frustrate you with one challeng…  Math Giraffe 25k Middle School Classroom,High School Students,High School Teachers,Middle School Tips,High School Counseling,Ela Classroom,High School Science,Future Classroom,Google Classroom image https://i.pinimg.com/originals/50/19/31/501931a27ee4d076658980851b995b2c.jpg 1 Local save in /data/education education 10794 c4bd2577-a7bb-4409-bb7a-17d5ed7e1cf1 TireBuyer Nissan GT-R. Sick. Ray Uyemura 437 Lowrider,Old Vintage Cars,Antique Cars,Austin Martin,Nissan Gtr Black,Jaguar,1959 Cadillac,Cadillac Ct6,Old School Cars image https://i.pinimg.com/originals/0d/29/9f/0d299f3df020395aa7ce8387f40fbeed.jpg 1 Local save in /data/vehicles vehicles 5494 8fb2af68-543b-4639-8119-de33d28706ed Dave Ramsey's 7 Baby Steps: What Are They And Will They Work For You If you love budgeting, make sure to give Dave Ramsey's 7 Baby Steps a try. Follow these steps to begin your debt snowball, build an emergency fund, invest and reach riches. I ca…  Living Low Key

In [ ]:
display(streaming_df_geo)

ind timestamp latitude longitude country 7528 2020-08-28T03:52:47.000+0000 -89.9787 -173.293 Albania 2863 2020-04-27T13:34:16.000+0000 -5.34445 -177.924 Armenia 5730 2021-04-19T17:37:03.000+0000 -77.015 -101.437 Colombia 8304 2019-09-13T04:50:29.000+0000 -28.8852 -164.87 French Guiana 8731 2020-07-17T04:39:09.000+0000 -83.104 -171.302 Aruba 1313 2018-06-26T02:39:25.000+0000 77.0447 61.9119 Maldives 4315 2019-12-15T03:51:28.000+0000 -45.8508 66.1003 Cote d'Ivoire 10794 2022-01-01T02:26:50.000+0000 -89.5236 -154.567 Cocos (Keeling) Islands 5494 2021-07-21T02:02:35.000+0000 -82.6768 -129.202 Bulgaria 5069 2021-03-20T09:32:44.000+0000 -63.0063 -157.474 Azerbaijan 2923 2019-09-08T22:53:09.000+0000 -84.6302 -164.507 Cote d'Ivoire 3089 2018-02-28T05:31:29.000+0000 -89.9787 -173.293 Albania 6063 2021-07-20T09:02:47.000+0000 -89.1797 -174.015 Anguilla 3454 2021-07-25T02:20:29.000+0000 -0.375174 49.8106 Cambodia 7554 2019-03-20T03:15:07.000+0000 -51.2172 -77.9768 Sudan 6145 2019-12-05T02:09:44.000+0000 -65.9079 -143.845 Mozambique 10625 2018-07-13T11:51:15.000+0000 -84.4944 -81.0613 Jamaica 2959 2019-08-19T08:22:02.000+0000 -68.0095 -157.227 Angola 9875 2020-03-20T13:03:18.000+0000 -74.3382 -110.484 Barbados 2418 2022-05-27T11:30:59.000+0000 -88.4642 -171.061 Antarctica (the territory South of 60 deg S) 3156 2018-01-13T19:33:49.000+0000 -84.738 -160.795 Armenia 428 2020-09-27T18:46:41.000+0000 -83.4105 -150.788 Bangladesh 7343 2018-08-06T12:17:07.000+0000 -65.4428 -161.684 Australia 2074 2019-11-03T05:41:59.000+0000 -52.3213 -50.11 Central African Republic 9979 2018-07-18T19:01:46.000+0000 14.9967 -120.682 Dominican Republic 10138 2019-08-03T00:59:29.000+0000 -72.142 -74.3545 Austria 9672 2019-11-03T13:15:52.000+0000 79.4658 -69.4133 India 8653 2022-04-11T18:30:19.000+0000 48.4569 -139.658 Seychelles 8887 2021-09-19T05:27:43.000+0000 -28.0137 -160.708 Botswana 7922 2021-01-27T09:14:19.000+0000 -88.0974 -172.052 Antigua and Barbuda 1014 2022-02-03T22:05:34.000+0000 81.1477 69.3538 Tonga 4913 2019-03-08T06:45:39.000+0000 -84.3768 -157.544 Aruba 4137 2019-06-23T22:16:34.000+0000 -55.3079 108.918 Australia 7166 2022-07-25T03:07:37.000+0000 -86.4063 -136.657 Aruba 9546 2018-02-10T06:16:40.000+0000 -70.0295 -155.428 Austria 2411 2020-11-15T17:10:07.000+0000 -71.6856 -179.126 Albania 9590 2019-05-20T19:48:48.000+0000 -64.3876 -174.281 Algeria 2698 2021-11-24T08:33:51.000+0000 -72.7174 24.169 Egypt 4508 2019-01-04T11:15:27.000+0000 69.1858 -76.0761 Philippines 831 2021-06-23T23:16:10.000+0000 -43.7816 -66.1592 Congo 5076 2019-05-05T16:22:23.000+0000 -70.7195 -91.1935 Germany 10663 2019-07-25T18:53:51.000+0000 -27.3474 -162.83 Saint Kitts and Nevis 5468 2020-05-16T23:17:50.000+0000 -83.544 33.9473 Isle of Man 205 2020-07-08T14:10:38.000+0000 -75.8378 -163.945 Barbados 7790 2018-07-31T08:19:15.000+0000 -43.692 64.9839 Papua New Guinea 8606 2021-03-28T14:54:07.000+0000 -88.0974 -172.052 Antigua and Barbuda 9759 2017-12-30T13:05:49.000+0000 -77.9744 -106.258 American Samoa 719 2018-10-29T04:05:12.000+0000 -38.4062 -154.323 Armenia 1704 2018-11-29T04:46:39.000+0000 -56.8702 -93.6232 Christmas Island 2482 2019-09-13T08:20:13.000+0000 63.4563 -164.709 Bermuda 8930 2021-09-29T13:25:49.000+0000 -89.4739 -176.154 Argentina 7294 2018-02-12T08:06:28.000+0000 -76.2967 -136.501 Australia 808 2019-01-03T15:43:12.000+0000 -71.6856 -179.126 Albania 771 2018-06-21T08:42:57.000+0000 -29.1712 -107.111 Montserrat 4076 2019-06-07T20:13:50.000+0000 -67.2157 27.8139 Mauritania 1545 2022-06-17T05:47:12.000+0000 -30.18 -72.3784 Anguilla 2293 2022-03-21T10:46:53.000+0000 -87.7946 -159.647 British Virgin Islands 10509 2019-03-06T12:21:56.000+0000 -67.187 -24.2977 Gibraltar 2015 2018-09-22T13:52:19.000+0000 -17.629 -177.685 Armenia 1094 2018-08-19T00:34:20.000+0000 -46.7328 -124.445 Armenia 603 2019-06-25T05:13:01.000+0000 14.0083 -141.603 Netherlands Antilles 7768 2018-05-25T21:34:19.000+0000 -88.355 -96.0131 Algeria 5630 2019-05-12T14:43:19.000+0000 -19.1403 -164.987 Bah

In [ ]:
display(streaming_df_user)

ind first_name last_name age date_joined 7528 Abigail Ali 20 2015-10-24T11:23:51.000+0000 2863 Dylan Holmes 32 2016-10-23T14:06:51.000+0000 5730 Rachel Davis 36 2015-12-08T20:02:43.000+0000 8304 Charles Berry 25 2015-12-28T04:21:39.000+0000 8731 Andrea Alexander 21 2015-11-10T09:27:42.000+0000 1313 Brittany Jones 32 2016-04-02T03:51:23.000+0000 4315 Michelle Prince 36 2015-12-20T16:38:13.000+0000 10794 Thomas Turner 34 2016-12-22T00:02:02.000+0000 5494 Anne Allen 27 2015-12-16T15:20:05.000+0000 5069 Amanda Ball 25 2016-01-13T17:36:30.000+0000 2923 Brian Nelson 26 2015-11-11T03:20:57.000+0000 3089 Abigail Ali 20 2015-10-24T11:23:51.000+0000 6063 Corey Andrews 23 2015-11-25T13:36:22.000+0000 3454 Robert Murphy 48 2017-09-26T16:31:56.000+0000 7554 Cheryl Huerta 20 2017-04-11T16:35:33.000+0000 6145 Emily Hawkins 30 2015-12-25T20:24:37.000+0000 10625 Christian Lang 32 2017-10-10T20:09:33.000+0000 2959 David Griffith 20 2016-01-07T19:49:22.000+0000 9875 Brendan Joseph 26 2015-12-20T10:28:00.000+0000 2418 Amanda Adams 20 2015-10-21T08:27:36.000+0000 3156 Andrew Baker 22 2015-12-21T08:06:54.000+0000 428 Claudia Adams 20 2015-11-28T02:20:29.000+0000 7343 Anne Clayton 24 2016-01-11T12:03:48.000+0000 2074 Annette Forbes 21 2016-01-03T15:42:12.000+0000 9979 Kaylee Miller 31 2016-11-09T19:50:51.000+0000 10138 Carol Silva 22 2015-12-31T14:57:02.000+0000 9672 Jennifer Hudson 22 2016-02-11T20:46:04.000+0000 8653 Tammy Davis 24 2016-03-09T10:48:14.000+0000 8887 Austin Rodriguez 24 2016-03-31T20:56:39.000+0000 7922 Denise Adams 21 2015-11-12T06:21:36.000+0000 1014 Gregory Ramsey 56 2016-10-15T17:21:39.000+0000 4913 Angela Brooks 24 2015-11-20T05:37:11.000+0000 4137 Michael Decker 59 2017-06-29T22:35:17.000+0000 7166 Alvin Adams 20 2016-01-01T13:50:40.000+0000 9546 Alex Barnes 20 2016-02-27T21:13:44.000+0000 2411 Aaron Bartlett 21 2015-11-24T02:15:36.000+0000 9590 Amanda Allen 22 2015-10-24T18:56:30.000+0000 2698 Kayla Burton 44 2017-06-21T19:53:27.000+0000 4508 Michael Carter 58 2016-06-03T23:35:30.000+0000 831 Aimee Collins 28 2016-06-16T02:06:38.000+0000 5076 Christopher Butler 20 2015-12-01T15:08:31.000+0000 10663 Julie Cox 23 2016-06-23T14:38:00.000+0000 5468 Lisa Gamble 20 2016-07-23T20:51:06.000+0000 205 Brett Bryant 20 2015-10-23T12:40:19.000+0000 7790 Michelle Gutierrez 39 2017-07-19T07:12:04.000+0000 8606 Denise Adams 21 2015-11-12T06:21:36.000+0000 9759 Daniel Brooks 25 2015-11-19T21:24:33.000+0000 719 Alicia Avila 20 2016-01-26T01:49:23.000+0000 1704 Barry Lynn 20 2015-10-28T05:00:33.000+0000 2482 David Moss 22 2016-03-01T07:11:48.000+0000 8930 Andrew Anderson 23 2015-11-28T11:52:37.000+0000 7294 Dawn Anderson 20 2016-12-31T00:06:36.000+0000 808 Aaron Bartlett 21 2015-11-24T02:15:36.000+0000 771 Brittany Butler 32 2016-03-10T04:11:31.000+0000 4076 Larry Pineda 20 2015-10-23T22:47:39.000+0000 1545 Jonathan Avila 46 2015-11-27T23:11:21.000+0000 2293 Alex Bean 24 2016-01-11T23:08:27.000+0000 10509 Brittany Thompson 49 2016-04-22T20:36:02.000+0000 2015 Christopher Bradshaw 27 2016-03-08T13:38:37.000+0000 1094 Ann Elliott 20 2016-07-02T02:32:30.000+0000 603 Brandon Jackson 44 2016-10-29T02:07:21.000+0000 7768 Christine Cortez 23 2015-12-01T18:15:02.000+0000 5630 Carlos Estrada 22 2016-02-09T17:01:38.000+0000 8578 Joe Pham 48 2017-06-01T23:13:27.000+0000 9936 Anthony Cantu 28 2016-11-15T10:40:03.000+0000 6844 Peter Roberts 30 2016-07-03T10:59:40.000+0000 3419 Aaron Jenkins 47 2017-04-26T03:26:23.000+0000 1268 Donna Campbell 32 2016-06-08T22:10:13.000+0000 6566 Alexander Perez 31 2017-08-04T14:30:22.000+0000 1555 Alexis Bennett 54 2016-05-15T04:22:01.000+0000 3729 Richard Edwards 52 2016-02-07T20:00:25.000+0000 6398 Christina Davenport 39 2016-06-29T20:43:59.000+0000 46 Erik Kelley 30 2016-01-06T09:58:56.000+0000 4988 Rhonda Durham 25 2017-07-20T05:51:23.000+0000 427 Jon Burke 25 2015-11-26T17:42:37.000+0000 3800 Adam Armstrong 20 2015-12-17T08:43:40.000+0000 159 Alison Bell 21 2016-01-07T08:11:35.000+0000 3599 Alexandria Alvarado 20 2015-1

## Cleaning Each DataFrame

In [ ]:
# Task 1: Clean the streaming_df_pin DataFrame

from pyspark.sql import SparkSession
from pyspark.sql import functions as F
from pyspark.sql.types import StructType, StructField, IntegerType, TimestampType, FloatType, StringType


# Replace empty entries and entries with no relevant data with Nones
streaming_df_pin = streaming_df_pin \
    .na.replace('', None) \
    .na.replace('NA', None)

# Perform necessary transformations on the follower_count column
streaming_df_pin = streaming_df_pin \
    .withColumn("follower_count", streaming_df_pin["follower_count"].cast("int"))

# Ensure that each column containing numeric data has a numeric data type
numeric_columns = ["downloaded", "index"]
for col_name in numeric_columns:
    streaming_df_pin = streaming_df_pin.withColumn(col_name, streaming_df_pin[col_name].cast("int"))

# Clean data in the save_location column to include only the save location path
streaming_df_pin = streaming_df_pin \
    .withColumn("save_location", F.regexp_extract("save_location", "(\/[^\/]+\/[^\/]+\/[^\/]+\/[^\/]+\/[^\/]+\/)", 1))

# Rename the index column to ind
streaming_df_pin = streaming_df_pin.withColumnRenamed("index", "ind")

# Reorder the DataFrame columns
streaming_df_pin = streaming_df_pin.select("ind", "unique_id", "title", "description", "follower_count", "poster_name",
                                           "tag_list", "is_image_or_video", "image_src", "save_location", "category")

# Display the cleaned DataFrame
display(streaming_df_pin)


ind unique_id title description follower_count poster_name tag_list is_image_or_video image_src save_location category 7528 fbe53c66-3442-4773-b19e-d3ec6f54dddf No Title Data Available No description available Story format null User Info Error N,o, ,T,a,g,s, ,A,v,a,i,l,a,b,l,e multi-video(story page format) Image src error. mens-fashion 2863 9bf39437-42a6-4f02-99a0-9a0383d8cd70 25 Super Fun Summer Crafts for Kids - Of Life and Lisa Keep the kids busy this summer with these easy diy crafts and projects. Creative and… null Of Life & Lisa | Lifestyle Blog Summer Crafts For Kids,Fun Crafts For Kids,Summer Kids,Toddler Crafts,Crafts To Do,Diy For Kids,Summer Snow,Diys For Summer,Craft Ideas For Girls image https://i.pinimg.com/originals/b3/bc/e2/b3bce2964e8c8975387b39660eed5f16.jpg diy-and-crafts 5730 1e1f0c8b-9fcf-460b-9154-c775827206eb Island Oasis Coupon Organizer Description Coupon Organizer in a fun colorful fabric -island oasis, Great Size for the "basic" couponer - holds up to 500 coupons with ease, and is made long enough so that you…  0 Consuelo Aguirre Grocery Items,Grocery Coupons,Care Organization,Coupon Organization,Extreme Couponing,Couponing 101,Life Binder,Save My Money,Love Coupons image https://i.pinimg.com/originals/65/bb/ea/65bbeaf458907bb079317d8303c4fa0e.jpg finance 8304 5b6d0913-25e4-43ab-839d-85d5516f78a4 The #1 Reason You’re Not His Priority Anymore - Matthew Coast #lovequotes #matchmaker #matchmadeinheaven #loveyourself #respectyourself null Commitment Connection Wise Quotes,Quotable Quotes,Words Quotes,Wise Words,Quotes To Live By,Great Quotes,Motivational Quotes,Inspirational Quotes,Funny Quotes image https://i.pinimg.com/originals/c6/64/ee/c664ee71524fb5a6e7b7b49233f93b43.png quotes 8731 ea760f71-febf-4023-b592-d17396659039 20 Koi Fish Tattoos For Lucky Men Koi fish tattoos are a popular choice for men who want to make a statement, thanks to their rich symbolism and bold design. null TheTrendSpotter Dr Tattoo,Wörter Tattoos,Pisces Tattoos,Tatoo Art,Dream Tattoos,Dope Tattoos,Mini Tattoos,Finger Tattoos,Body Art Tattoos image https://i.pinimg.com/originals/8a/0c/0a/8a0c0a7b6236565c519acd41ad1a52c0.jpg tattoos 1313 44662045-e891-4821-8a19-ebe7eedd371a Liquid Lash Extensions Mascara Instantly create the look of lash extensions with this award-winning, best-selling mascara that won't clump, flake or smudge. Available in 3 shades! null Thrive Causemetics N,o, ,T,a,g,s, ,A,v,a,i,l,a,b,l,e video https://i.pinimg.com/videos/thumbnails/originals/69/84/e2/6984e20f3e262098fa9c0614c3453254.0000001.jpg beauty 4315 21b59ba9-829d-4c33-8c27-4cd4c56d26b8 Podcasts for Teachers or Parents of Teenagers Podcasts for Teachers or Parents of Teenagers: Teaching teens middle school and high school can feel joyful and rewarding most days, but can also frustrate you with one challeng…  null Math Giraffe Middle School Classroom,High School Students,High School Teachers,Middle School Tips,High School Counseling,Ela Classroom,High School Science,Future Classroom,Google Classroom image https://i.pinimg.com/originals/50/19/31/501931a27ee4d076658980851b995b2c.jpg education 10794 c4bd2577-a7bb-4409-bb7a-17d5ed7e1cf1 TireBuyer Nissan GT-R. Sick. 437 Ray Uyemura Lowrider,Old Vintage Cars,Antique Cars,Austin Martin,Nissan Gtr Black,Jaguar,1959 Cadillac,Cadillac Ct6,Old School Cars image https://i.pinimg.com/originals/0d/29/9f/0d299f3df020395aa7ce8387f40fbeed.jpg vehicles 5494 8fb2af68-543b-4639-8119-de33d28706ed Dave Ramsey's 7 Baby Steps: What Are They And Will They Work For You If you love budgeting, make sure to give Dave Ramsey's 7 Baby Steps a try. Follow these steps to begin your debt snowball, build an emergency fund, invest and reach riches. I ca…  null Living Low Key | Save Money, Make Money, & Frugal Living Financial Peace,Financial Tips,Saving Money Quotes,Total Money Makeover,Budgeting Finances,Money Management,Wealth Management,Personal Finance,Making Ideas image https://i.pinimg.com/originals/1e/9d/90/1e9d906e4e150e3b95187f3b

In [ ]:
streaming_df_pin.printSchema()

root
-- ind: integer (nullable = true)
-- unique_id: string (nullable = true)
-- title: string (nullable = true)
-- description: string (nullable = true)
-- follower_count: integer (nullable = true)
-- poster_name: string (nullable = true)
-- tag_list: string (nullable = true)
-- is_image_or_video: string (nullable = true)
-- image_src: string (nullable = true)
-- save_location: string (nullable = true)
-- category: string (nullable = true)

In [ ]:
# Task 2: Clean the streaming_df_geo DataFrame

from pyspark.sql import SparkSession
from pyspark.sql import functions as F
from pyspark.sql.types import StructType, StructField, IntegerType, TimestampType, FloatType, StringType

# Assuming streaming_df_geo is your streaming DataFrame
# Make sure to replace streaming_df_geo with the actual DataFrame variable name

# Print the schema of the streaming DataFrame
streaming_df_geo.printSchema()

# Replace empty entries and entries with no relevant data with Nones
streaming_df_geo = streaming_df_geo \
    .na.replace('', None) \
    .na.replace('NA', None)

# Convert the timestamp column from a string to a timestamp data type
streaming_df_geo = streaming_df_geo.withColumn("timestamp", F.to_timestamp("timestamp"))

# Reorder the DataFrame columns
streaming_df_geo = streaming_df_geo.select("ind", "country", "timestamp")

# Display the cleaned DataFrame
display(streaming_df_geo)


ind country timestamp 7528 Albania 2020-08-28T03:52:47.000+0000 2863 Armenia 2020-04-27T13:34:16.000+0000 5730 Colombia 2021-04-19T17:37:03.000+0000 8304 French Guiana 2019-09-13T04:50:29.000+0000 8731 Aruba 2020-07-17T04:39:09.000+0000 1313 Maldives 2018-06-26T02:39:25.000+0000 4315 Cote d'Ivoire 2019-12-15T03:51:28.000+0000 10794 Cocos (Keeling) Islands 2022-01-01T02:26:50.000+0000 5494 Bulgaria 2021-07-21T02:02:35.000+0000 5069 Azerbaijan 2021-03-20T09:32:44.000+0000 2923 Cote d'Ivoire 2019-09-08T22:53:09.000+0000 3089 Albania 2018-02-28T05:31:29.000+0000 6063 Anguilla 2021-07-20T09:02:47.000+0000 3454 Cambodia 2021-07-25T02:20:29.000+0000 7554 Sudan 2019-03-20T03:15:07.000+0000 6145 Mozambique 2019-12-05T02:09:44.000+0000 10625 Jamaica 2018-07-13T11:51:15.000+0000 2959 Angola 2019-08-19T08:22:02.000+0000 9875 Barbados 2020-03-20T13:03:18.000+0000 2418 Antarctica (the territory South of 60 deg S) 2022-05-27T11:30:59.000+0000 3156 Armenia 2018-01-13T19:33:49.000+0000 428 Bangladesh 2020-09-27T18:46:41.000+0000 7343 Australia 2018-08-06T12:17:07.000+0000 2074 Central African Republic 2019-11-03T05:41:59.000+0000 9979 Dominican Republic 2018-07-18T19:01:46.000+0000 10138 Austria 2019-08-03T00:59:29.000+0000 9672 India 2019-11-03T13:15:52.000+0000 8653 Seychelles 2022-04-11T18:30:19.000+0000 8887 Botswana 2021-09-19T05:27:43.000+0000 7922 Antigua and Barbuda 2021-01-27T09:14:19.000+0000 1014 Tonga 2022-02-03T22:05:34.000+0000 4913 Aruba 2019-03-08T06:45:39.000+0000 4137 Australia 2019-06-23T22:16:34.000+0000 7166 Aruba 2022-07-25T03:07:37.000+0000 9546 Austria 2018-02-10T06:16:40.000+0000 2411 Albania 2020-11-15T17:10:07.000+0000 9590 Algeria 2019-05-20T19:48:48.000+0000 2698 Egypt 2021-11-24T08:33:51.000+0000 4508 Philippines 2019-01-04T11:15:27.000+0000 831 Congo 2021-06-23T23:16:10.000+0000 5076 Germany 2019-05-05T16:22:23.000+0000 10663 Saint Kitts and Nevis 2019-07-25T18:53:51.000+0000 5468 Isle of Man 2020-05-16T23:17:50.000+0000 205 Barbados 2020-07-08T14:10:38.000+0000 7790 Papua New Guinea 2018-07-31T08:19:15.000+0000 8606 Antigua and Barbuda 2021-03-28T14:54:07.000+0000 9759 American Samoa 2017-12-30T13:05:49.000+0000 719 Armenia 2018-10-29T04:05:12.000+0000 1704 Christmas Island 2018-11-29T04:46:39.000+0000 2482 Bermuda 2019-09-13T08:20:13.000+0000 8930 Argentina 2021-09-29T13:25:49.000+0000 7294 Australia 2018-02-12T08:06:28.000+0000 808 Albania 2019-01-03T15:43:12.000+0000 771 Montserrat 2018-06-21T08:42:57.000+0000 4076 Mauritania 2019-06-07T20:13:50.000+0000 1545 Anguilla 2022-06-17T05:47:12.000+0000 2293 British Virgin Islands 2022-03-21T10:46:53.000+0000 10509 Gibraltar 2019-03-06T12:21:56.000+0000 2015 Armenia 2018-09-22T13:52:19.000+0000 1094 Armenia 2018-08-19T00:34:20.000+0000 603 Netherlands Antilles 2019-06-25T05:13:01.000+0000 7768 Algeria 2018-05-25T21:34:19.000+0000 5630 Bahrain 2019-05-12T14:43:19.000+0000 8578 Guinea-Bissau 2018-01-26T19:27:11.000+0000 9936 Australia 2018-06-30T22:07:13.000+0000 6844 New Caledonia 2021-06-06T21:53:11.000+0000 3419 Bhutan 2021-12-20T05:01:54.000+0000 1268 Argentina 2019-07-06T04:10:29.000+0000 6566 Cape Verde 2020-11-19T10:06:13.000+0000 1555 Algeria 2017-12-24T18:41:23.000+0000 3729 Turkey 2018-01-17T03:43:38.000+0000 6398 Albania 2020-01-19T01:49:05.000+0000 46 Afghanistan 2018-09-15T09:16:57.000+0000 4988 Madagascar 2020-07-11T11:01:12.000+0000 427 Isle of Man 2020-04-22T03:08:50.000+0000 3800 Aruba 2018-01-27T16:49:07.000+0000 159 Andorra 2017-11-20T21:14:56.000+0000 3599 Afghanistan 2019-03-03T06:13:41.000+0000 10552 Grenada 2020-08-24T11:39:32.000+0000 1422 American Samoa 2018-04-30T08:27:21.000+0000 5309 Maldives 2020-05-04T22:00:32.000+0000 552 Lesotho 2022-03-14T05:12:07.000+0000 1371 Andorra 2018-08-08T04:41:17.000+0000 10119 Christmas Island 2020-10-22T01:59:58.000+0000 9074 Andorra 2022-04-10T17:06:13.000+0000 2604 Antigua and Barbuda 2018-12-01T09:23:35.000+0000 223 Isle of Man 2018-12-07T07:30:40.000+0000 8312 American Samoa 2021-04-25T15:56:29.000+0000 

In [ ]:
streaming_df_geo.printSchema()

root
-- ind: integer (nullable = true)
-- country: string (nullable = true)
-- timestamp: timestamp (nullable = true)

In [ ]:
streaming_df_user.printSchema()

root
-- ind: integer (nullable = true)
-- first_name: string (nullable = true)
-- last_name: string (nullable = true)
-- age: string (nullable = true)
-- date_joined: timestamp (nullable = true)

In [ ]:
# Task 3: Clean the streaming_df_user DataFrame

from pyspark.sql import SparkSession
from pyspark.sql import functions as F
from pyspark.sql.types import StructType, StructField, IntegerType, TimestampType, FloatType, StringType

# Assuming streaming_df_user is your streaming DataFrame
# Make sure to replace streaming_df_user with the actual DataFrame variable name

# Print the schema of the streaming DataFrame
streaming_df_user.printSchema()

# Replace empty entries and entries with no relevant data with Nones
streaming_df_user = streaming_df_user \
    .na.replace('', None) \
    .na.replace('NA', None)

# Create a new column 'user_name' that concatenates the information found in the first_name and last_name columns
streaming_df_user = streaming_df_user.withColumn("user_name", F.concat_ws(" ", "first_name", "last_name"))

# Drop the first_name and last_name columns from the DataFrame
streaming_df_user = streaming_df_user.drop("first_name", "last_name")

# Convert the date_joined column from a string to a timestamp data type
streaming_df_user = streaming_df_user.withColumn("date_joined", F.to_timestamp("date_joined"))

# Reorder the DataFrame columns
streaming_df_user = streaming_df_user.select("ind", "user_name", "age", "date_joined")

# Display the cleaned DataFrame
display(streaming_df_user)


ind user_name age date_joined 7528 Abigail Ali 20 2015-10-24T11:23:51.000+0000 2863 Dylan Holmes 32 2016-10-23T14:06:51.000+0000 5730 Rachel Davis 36 2015-12-08T20:02:43.000+0000 8304 Charles Berry 25 2015-12-28T04:21:39.000+0000 8731 Andrea Alexander 21 2015-11-10T09:27:42.000+0000 1313 Brittany Jones 32 2016-04-02T03:51:23.000+0000 4315 Michelle Prince 36 2015-12-20T16:38:13.000+0000 10794 Thomas Turner 34 2016-12-22T00:02:02.000+0000 5494 Anne Allen 27 2015-12-16T15:20:05.000+0000 5069 Amanda Ball 25 2016-01-13T17:36:30.000+0000 2923 Brian Nelson 26 2015-11-11T03:20:57.000+0000 3089 Abigail Ali 20 2015-10-24T11:23:51.000+0000 6063 Corey Andrews 23 2015-11-25T13:36:22.000+0000 3454 Robert Murphy 48 2017-09-26T16:31:56.000+0000 7554 Cheryl Huerta 20 2017-04-11T16:35:33.000+0000 6145 Emily Hawkins 30 2015-12-25T20:24:37.000+0000 10625 Christian Lang 32 2017-10-10T20:09:33.000+0000 2959 David Griffith 20 2016-01-07T19:49:22.000+0000 9875 Brendan Joseph 26 2015-12-20T10:28:00.000+0000 2418 Amanda Adams 20 2015-10-21T08:27:36.000+0000 3156 Andrew Baker 22 2015-12-21T08:06:54.000+0000 428 Claudia Adams 20 2015-11-28T02:20:29.000+0000 7343 Anne Clayton 24 2016-01-11T12:03:48.000+0000 2074 Annette Forbes 21 2016-01-03T15:42:12.000+0000 9979 Kaylee Miller 31 2016-11-09T19:50:51.000+0000 10138 Carol Silva 22 2015-12-31T14:57:02.000+0000 9672 Jennifer Hudson 22 2016-02-11T20:46:04.000+0000 8653 Tammy Davis 24 2016-03-09T10:48:14.000+0000 8887 Austin Rodriguez 24 2016-03-31T20:56:39.000+0000 7922 Denise Adams 21 2015-11-12T06:21:36.000+0000 1014 Gregory Ramsey 56 2016-10-15T17:21:39.000+0000 4913 Angela Brooks 24 2015-11-20T05:37:11.000+0000 4137 Michael Decker 59 2017-06-29T22:35:17.000+0000 7166 Alvin Adams 20 2016-01-01T13:50:40.000+0000 9546 Alex Barnes 20 2016-02-27T21:13:44.000+0000 2411 Aaron Bartlett 21 2015-11-24T02:15:36.000+0000 9590 Amanda Allen 22 2015-10-24T18:56:30.000+0000 2698 Kayla Burton 44 2017-06-21T19:53:27.000+0000 4508 Michael Carter 58 2016-06-03T23:35:30.000+0000 831 Aimee Collins 28 2016-06-16T02:06:38.000+0000 5076 Christopher Butler 20 2015-12-01T15:08:31.000+0000 10663 Julie Cox 23 2016-06-23T14:38:00.000+0000 5468 Lisa Gamble 20 2016-07-23T20:51:06.000+0000 205 Brett Bryant 20 2015-10-23T12:40:19.000+0000 7790 Michelle Gutierrez 39 2017-07-19T07:12:04.000+0000 8606 Denise Adams 21 2015-11-12T06:21:36.000+0000 9759 Daniel Brooks 25 2015-11-19T21:24:33.000+0000 719 Alicia Avila 20 2016-01-26T01:49:23.000+0000 1704 Barry Lynn 20 2015-10-28T05:00:33.000+0000 2482 David Moss 22 2016-03-01T07:11:48.000+0000 8930 Andrew Anderson 23 2015-11-28T11:52:37.000+0000 7294 Dawn Anderson 20 2016-12-31T00:06:36.000+0000 808 Aaron Bartlett 21 2015-11-24T02:15:36.000+0000 771 Brittany Butler 32 2016-03-10T04:11:31.000+0000 4076 Larry Pineda 20 2015-10-23T22:47:39.000+0000 1545 Jonathan Avila 46 2015-11-27T23:11:21.000+0000 2293 Alex Bean 24 2016-01-11T23:08:27.000+0000 10509 Brittany Thompson 49 2016-04-22T20:36:02.000+0000 2015 Christopher Bradshaw 27 2016-03-08T13:38:37.000+0000 1094 Ann Elliott 20 2016-07-02T02:32:30.000+0000 603 Brandon Jackson 44 2016-10-29T02:07:21.000+0000 7768 Christine Cortez 23 2015-12-01T18:15:02.000+0000 5630 Carlos Estrada 22 2016-02-09T17:01:38.000+0000 8578 Joe Pham 48 2017-06-01T23:13:27.000+0000 9936 Anthony Cantu 28 2016-11-15T10:40:03.000+0000 6844 Peter Roberts 30 2016-07-03T10:59:40.000+0000 3419 Aaron Jenkins 47 2017-04-26T03:26:23.000+0000 1268 Donna Campbell 32 2016-06-08T22:10:13.000+0000 6566 Alexander Perez 31 2017-08-04T14:30:22.000+0000 1555 Alexis Bennett 54 2016-05-15T04:22:01.000+0000 3729 Richard Edwards 52 2016-02-07T20:00:25.000+0000 6398 Christina Davenport 39 2016-06-29T20:43:59.000+0000 46 Erik Kelley 30 2016-01-06T09:58:56.000+0000 4988 Rhonda Durham 25 2017-07-20T05:51:23.000+0000 427 Jon Burke 25 2015-11-26T17:42:37.000+0000 3800 Adam Armstrong 20 2015-12-17T08:43:40.000+0000 159 Alison Bell 21 2016-01-07T08:11:35.000+0000 3599 Alexandria Alvarado 20 2015-10-23T04:13:

In [ ]:
streaming_df_user.printSchema()

root
-- ind: integer (nullable = true)
-- user_name: string (nullable = false)
-- age: string (nullable = true)
-- date_joined: timestamp (nullable = true)

## Display the Dataframes

In [ ]:
display(streaming_df_pin)

ind unique_id title description follower_count poster_name tag_list is_image_or_video image_src save_location category 7528 fbe53c66-3442-4773-b19e-d3ec6f54dddf No Title Data Available No description available Story format null User Info Error N,o, ,T,a,g,s, ,A,v,a,i,l,a,b,l,e multi-video(story page format) Image src error. mens-fashion 2863 9bf39437-42a6-4f02-99a0-9a0383d8cd70 25 Super Fun Summer Crafts for Kids - Of Life and Lisa Keep the kids busy this summer with these easy diy crafts and projects. Creative and… null Of Life & Lisa | Lifestyle Blog Summer Crafts For Kids,Fun Crafts For Kids,Summer Kids,Toddler Crafts,Crafts To Do,Diy For Kids,Summer Snow,Diys For Summer,Craft Ideas For Girls image https://i.pinimg.com/originals/b3/bc/e2/b3bce2964e8c8975387b39660eed5f16.jpg diy-and-crafts 5730 1e1f0c8b-9fcf-460b-9154-c775827206eb Island Oasis Coupon Organizer Description Coupon Organizer in a fun colorful fabric -island oasis, Great Size for the "basic" couponer - holds up to 500 coupons with ease, and is made long enough so that you…  0 Consuelo Aguirre Grocery Items,Grocery Coupons,Care Organization,Coupon Organization,Extreme Couponing,Couponing 101,Life Binder,Save My Money,Love Coupons image https://i.pinimg.com/originals/65/bb/ea/65bbeaf458907bb079317d8303c4fa0e.jpg finance 8304 5b6d0913-25e4-43ab-839d-85d5516f78a4 The #1 Reason You’re Not His Priority Anymore - Matthew Coast #lovequotes #matchmaker #matchmadeinheaven #loveyourself #respectyourself null Commitment Connection Wise Quotes,Quotable Quotes,Words Quotes,Wise Words,Quotes To Live By,Great Quotes,Motivational Quotes,Inspirational Quotes,Funny Quotes image https://i.pinimg.com/originals/c6/64/ee/c664ee71524fb5a6e7b7b49233f93b43.png quotes 8731 ea760f71-febf-4023-b592-d17396659039 20 Koi Fish Tattoos For Lucky Men Koi fish tattoos are a popular choice for men who want to make a statement, thanks to their rich symbolism and bold design. null TheTrendSpotter Dr Tattoo,Wörter Tattoos,Pisces Tattoos,Tatoo Art,Dream Tattoos,Dope Tattoos,Mini Tattoos,Finger Tattoos,Body Art Tattoos image https://i.pinimg.com/originals/8a/0c/0a/8a0c0a7b6236565c519acd41ad1a52c0.jpg tattoos 1313 44662045-e891-4821-8a19-ebe7eedd371a Liquid Lash Extensions Mascara Instantly create the look of lash extensions with this award-winning, best-selling mascara that won't clump, flake or smudge. Available in 3 shades! null Thrive Causemetics N,o, ,T,a,g,s, ,A,v,a,i,l,a,b,l,e video https://i.pinimg.com/videos/thumbnails/originals/69/84/e2/6984e20f3e262098fa9c0614c3453254.0000001.jpg beauty 4315 21b59ba9-829d-4c33-8c27-4cd4c56d26b8 Podcasts for Teachers or Parents of Teenagers Podcasts for Teachers or Parents of Teenagers: Teaching teens middle school and high school can feel joyful and rewarding most days, but can also frustrate you with one challeng…  null Math Giraffe Middle School Classroom,High School Students,High School Teachers,Middle School Tips,High School Counseling,Ela Classroom,High School Science,Future Classroom,Google Classroom image https://i.pinimg.com/originals/50/19/31/501931a27ee4d076658980851b995b2c.jpg education 10794 c4bd2577-a7bb-4409-bb7a-17d5ed7e1cf1 TireBuyer Nissan GT-R. Sick. 437 Ray Uyemura Lowrider,Old Vintage Cars,Antique Cars,Austin Martin,Nissan Gtr Black,Jaguar,1959 Cadillac,Cadillac Ct6,Old School Cars image https://i.pinimg.com/originals/0d/29/9f/0d299f3df020395aa7ce8387f40fbeed.jpg vehicles 5494 8fb2af68-543b-4639-8119-de33d28706ed Dave Ramsey's 7 Baby Steps: What Are They And Will They Work For You If you love budgeting, make sure to give Dave Ramsey's 7 Baby Steps a try. Follow these steps to begin your debt snowball, build an emergency fund, invest and reach riches. I ca…  null Living Low Key | Save Money, Make Money, & Frugal Living Financial Peace,Financial Tips,Saving Money Quotes,Total Money Makeover,Budgeting Finances,Money Management,Wealth Management,Personal Finance,Making Ideas image https://i.pinimg.com/originals/1e/9d/90/1e9d906e4e150e3b95187f3b

In [ ]:
display(streaming_df_geo)

ind country timestamp 7528 Albania 2020-08-28T03:52:47.000+0000 2863 Armenia 2020-04-27T13:34:16.000+0000 5730 Colombia 2021-04-19T17:37:03.000+0000 8304 French Guiana 2019-09-13T04:50:29.000+0000 8731 Aruba 2020-07-17T04:39:09.000+0000 1313 Maldives 2018-06-26T02:39:25.000+0000 4315 Cote d'Ivoire 2019-12-15T03:51:28.000+0000 10794 Cocos (Keeling) Islands 2022-01-01T02:26:50.000+0000 5494 Bulgaria 2021-07-21T02:02:35.000+0000 5069 Azerbaijan 2021-03-20T09:32:44.000+0000 2923 Cote d'Ivoire 2019-09-08T22:53:09.000+0000 3089 Albania 2018-02-28T05:31:29.000+0000 6063 Anguilla 2021-07-20T09:02:47.000+0000 3454 Cambodia 2021-07-25T02:20:29.000+0000 7554 Sudan 2019-03-20T03:15:07.000+0000 6145 Mozambique 2019-12-05T02:09:44.000+0000 10625 Jamaica 2018-07-13T11:51:15.000+0000 2959 Angola 2019-08-19T08:22:02.000+0000 9875 Barbados 2020-03-20T13:03:18.000+0000 2418 Antarctica (the territory South of 60 deg S) 2022-05-27T11:30:59.000+0000 3156 Armenia 2018-01-13T19:33:49.000+0000 428 Bangladesh 2020-09-27T18:46:41.000+0000 7343 Australia 2018-08-06T12:17:07.000+0000 2074 Central African Republic 2019-11-03T05:41:59.000+0000 9979 Dominican Republic 2018-07-18T19:01:46.000+0000 10138 Austria 2019-08-03T00:59:29.000+0000 9672 India 2019-11-03T13:15:52.000+0000 8653 Seychelles 2022-04-11T18:30:19.000+0000 8887 Botswana 2021-09-19T05:27:43.000+0000 7922 Antigua and Barbuda 2021-01-27T09:14:19.000+0000 1014 Tonga 2022-02-03T22:05:34.000+0000 4913 Aruba 2019-03-08T06:45:39.000+0000 4137 Australia 2019-06-23T22:16:34.000+0000 7166 Aruba 2022-07-25T03:07:37.000+0000 9546 Austria 2018-02-10T06:16:40.000+0000 2411 Albania 2020-11-15T17:10:07.000+0000 9590 Algeria 2019-05-20T19:48:48.000+0000 2698 Egypt 2021-11-24T08:33:51.000+0000 4508 Philippines 2019-01-04T11:15:27.000+0000 831 Congo 2021-06-23T23:16:10.000+0000 5076 Germany 2019-05-05T16:22:23.000+0000 10663 Saint Kitts and Nevis 2019-07-25T18:53:51.000+0000 5468 Isle of Man 2020-05-16T23:17:50.000+0000 205 Barbados 2020-07-08T14:10:38.000+0000 7790 Papua New Guinea 2018-07-31T08:19:15.000+0000 8606 Antigua and Barbuda 2021-03-28T14:54:07.000+0000 9759 American Samoa 2017-12-30T13:05:49.000+0000 719 Armenia 2018-10-29T04:05:12.000+0000 1704 Christmas Island 2018-11-29T04:46:39.000+0000 2482 Bermuda 2019-09-13T08:20:13.000+0000 8930 Argentina 2021-09-29T13:25:49.000+0000 7294 Australia 2018-02-12T08:06:28.000+0000 808 Albania 2019-01-03T15:43:12.000+0000 771 Montserrat 2018-06-21T08:42:57.000+0000 4076 Mauritania 2019-06-07T20:13:50.000+0000 1545 Anguilla 2022-06-17T05:47:12.000+0000 2293 British Virgin Islands 2022-03-21T10:46:53.000+0000 10509 Gibraltar 2019-03-06T12:21:56.000+0000 2015 Armenia 2018-09-22T13:52:19.000+0000 1094 Armenia 2018-08-19T00:34:20.000+0000 603 Netherlands Antilles 2019-06-25T05:13:01.000+0000 7768 Algeria 2018-05-25T21:34:19.000+0000 5630 Bahrain 2019-05-12T14:43:19.000+0000 8578 Guinea-Bissau 2018-01-26T19:27:11.000+0000 9936 Australia 2018-06-30T22:07:13.000+0000 6844 New Caledonia 2021-06-06T21:53:11.000+0000 3419 Bhutan 2021-12-20T05:01:54.000+0000 1268 Argentina 2019-07-06T04:10:29.000+0000 6566 Cape Verde 2020-11-19T10:06:13.000+0000 1555 Algeria 2017-12-24T18:41:23.000+0000 3729 Turkey 2018-01-17T03:43:38.000+0000 6398 Albania 2020-01-19T01:49:05.000+0000 46 Afghanistan 2018-09-15T09:16:57.000+0000 4988 Madagascar 2020-07-11T11:01:12.000+0000 427 Isle of Man 2020-04-22T03:08:50.000+0000 3800 Aruba 2018-01-27T16:49:07.000+0000 159 Andorra 2017-11-20T21:14:56.000+0000 3599 Afghanistan 2019-03-03T06:13:41.000+0000 10552 Grenada 2020-08-24T11:39:32.000+0000 1422 American Samoa 2018-04-30T08:27:21.000+0000 5309 Maldives 2020-05-04T22:00:32.000+0000 552 Lesotho 2022-03-14T05:12:07.000+0000 1371 Andorra 2018-08-08T04:41:17.000+0000 10119 Christmas Island 2020-10-22T01:59:58.000+0000 9074 Andorra 2022-04-10T17:06:13.000+0000 2604 Antigua and Barbuda 2018-12-01T09:23:35.000+0000 223 Isle of Man 2018-12-07T07:30:40.000+0000 8312 American Samoa 2021-04-25T15:56:29.000+0000 

In [ ]:
display(streaming_df_user)

ind user_name age date_joined 7528 Abigail Ali 20 2015-10-24T11:23:51.000+0000 2863 Dylan Holmes 32 2016-10-23T14:06:51.000+0000 5730 Rachel Davis 36 2015-12-08T20:02:43.000+0000 8304 Charles Berry 25 2015-12-28T04:21:39.000+0000 8731 Andrea Alexander 21 2015-11-10T09:27:42.000+0000 1313 Brittany Jones 32 2016-04-02T03:51:23.000+0000 4315 Michelle Prince 36 2015-12-20T16:38:13.000+0000 10794 Thomas Turner 34 2016-12-22T00:02:02.000+0000 5494 Anne Allen 27 2015-12-16T15:20:05.000+0000 5069 Amanda Ball 25 2016-01-13T17:36:30.000+0000 2923 Brian Nelson 26 2015-11-11T03:20:57.000+0000 3089 Abigail Ali 20 2015-10-24T11:23:51.000+0000 6063 Corey Andrews 23 2015-11-25T13:36:22.000+0000 3454 Robert Murphy 48 2017-09-26T16:31:56.000+0000 7554 Cheryl Huerta 20 2017-04-11T16:35:33.000+0000 6145 Emily Hawkins 30 2015-12-25T20:24:37.000+0000 10625 Christian Lang 32 2017-10-10T20:09:33.000+0000 2959 David Griffith 20 2016-01-07T19:49:22.000+0000 9875 Brendan Joseph 26 2015-12-20T10:28:00.000+0000 2418 Amanda Adams 20 2015-10-21T08:27:36.000+0000 3156 Andrew Baker 22 2015-12-21T08:06:54.000+0000 428 Claudia Adams 20 2015-11-28T02:20:29.000+0000 7343 Anne Clayton 24 2016-01-11T12:03:48.000+0000 2074 Annette Forbes 21 2016-01-03T15:42:12.000+0000 9979 Kaylee Miller 31 2016-11-09T19:50:51.000+0000 10138 Carol Silva 22 2015-12-31T14:57:02.000+0000 9672 Jennifer Hudson 22 2016-02-11T20:46:04.000+0000 8653 Tammy Davis 24 2016-03-09T10:48:14.000+0000 8887 Austin Rodriguez 24 2016-03-31T20:56:39.000+0000 7922 Denise Adams 21 2015-11-12T06:21:36.000+0000 1014 Gregory Ramsey 56 2016-10-15T17:21:39.000+0000 4913 Angela Brooks 24 2015-11-20T05:37:11.000+0000 4137 Michael Decker 59 2017-06-29T22:35:17.000+0000 7166 Alvin Adams 20 2016-01-01T13:50:40.000+0000 9546 Alex Barnes 20 2016-02-27T21:13:44.000+0000 2411 Aaron Bartlett 21 2015-11-24T02:15:36.000+0000 9590 Amanda Allen 22 2015-10-24T18:56:30.000+0000 2698 Kayla Burton 44 2017-06-21T19:53:27.000+0000 4508 Michael Carter 58 2016-06-03T23:35:30.000+0000 831 Aimee Collins 28 2016-06-16T02:06:38.000+0000 5076 Christopher Butler 20 2015-12-01T15:08:31.000+0000 10663 Julie Cox 23 2016-06-23T14:38:00.000+0000 5468 Lisa Gamble 20 2016-07-23T20:51:06.000+0000 205 Brett Bryant 20 2015-10-23T12:40:19.000+0000 7790 Michelle Gutierrez 39 2017-07-19T07:12:04.000+0000 8606 Denise Adams 21 2015-11-12T06:21:36.000+0000 9759 Daniel Brooks 25 2015-11-19T21:24:33.000+0000 719 Alicia Avila 20 2016-01-26T01:49:23.000+0000 1704 Barry Lynn 20 2015-10-28T05:00:33.000+0000 2482 David Moss 22 2016-03-01T07:11:48.000+0000 8930 Andrew Anderson 23 2015-11-28T11:52:37.000+0000 7294 Dawn Anderson 20 2016-12-31T00:06:36.000+0000 808 Aaron Bartlett 21 2015-11-24T02:15:36.000+0000 771 Brittany Butler 32 2016-03-10T04:11:31.000+0000 4076 Larry Pineda 20 2015-10-23T22:47:39.000+0000 1545 Jonathan Avila 46 2015-11-27T23:11:21.000+0000 2293 Alex Bean 24 2016-01-11T23:08:27.000+0000 10509 Brittany Thompson 49 2016-04-22T20:36:02.000+0000 2015 Christopher Bradshaw 27 2016-03-08T13:38:37.000+0000 1094 Ann Elliott 20 2016-07-02T02:32:30.000+0000 603 Brandon Jackson 44 2016-10-29T02:07:21.000+0000 7768 Christine Cortez 23 2015-12-01T18:15:02.000+0000 5630 Carlos Estrada 22 2016-02-09T17:01:38.000+0000 8578 Joe Pham 48 2017-06-01T23:13:27.000+0000 9936 Anthony Cantu 28 2016-11-15T10:40:03.000+0000 6844 Peter Roberts 30 2016-07-03T10:59:40.000+0000 3419 Aaron Jenkins 47 2017-04-26T03:26:23.000+0000 1268 Donna Campbell 32 2016-06-08T22:10:13.000+0000 6566 Alexander Perez 31 2017-08-04T14:30:22.000+0000 1555 Alexis Bennett 54 2016-05-15T04:22:01.000+0000 3729 Richard Edwards 52 2016-02-07T20:00:25.000+0000 6398 Christina Davenport 39 2016-06-29T20:43:59.000+0000 46 Erik Kelley 30 2016-01-06T09:58:56.000+0000 4988 Rhonda Durham 25 2017-07-20T05:51:23.000+0000 427 Jon Burke 25 2015-11-26T17:42:37.000+0000 3800 Adam Armstrong 20 2015-12-17T08:43:40.000+0000 159 Alison Bell 21 2016-01-07T08:11:35.000+0000 3599 Alexandria Alvarado 20 2015-10-23T04:13:

##Write Data to Delta Tables


In [ ]:
from pyspark.sql import SparkSession

# streaming_df_pin, streaming_df_geo, streaming_df_user

# Define Delta table names
pin_delta_table = "streaming_df_pin_table"
geo_delta_table = "streaming_df_geo_table"
user_delta_table = "streaming_df_user_table"

# Create a SparkSession 
spark = SparkSession.builder.appName("WriteStreamsToDelta").getOrCreate()

# Define a function to write a DataFrame to a Delta table
def write_to_delta(df, delta_table):  # Pass the DataFrame directly
    query = (
        df.writeStream
        .format("delta")
        .option("checkpointLocation", f"dbfs:/user/hive/warehouse/{delta_table}")
        .outputMode("append")
        .table(delta_table)
    )
    query.awaitTermination()

# Write each streaming DataFrame to its corresponding Delta table
write_to_delta(streaming_df_pin, pin_delta_table)
write_to_delta(streaming_df_geo, geo_delta_table)
write_to_delta(streaming_df_user, user_delta_table)

# Stop the SparkSession (if necessary)
spark.stop()
